Copyright (C) 2019 Elvis Yu-Jing Lin <elvisyjlin@gmail.com>

This work is licensed under the Creative Commons Attribution-NonCommercial
4.0 International License. To view a copy of this license, visit
http://creativecommons.org/licenses/by-nc/4.0/ or send a letter to
Creative Commons, PO Box 1866, Mountain View, CA 94042, USA.

In [1]:
# Import all used packages

import argparse
import json
import numpy as np
import os
import pandas as pd
import time
from datetime import datetime, timedelta
from tqdm import tqdm

from summary import TxHistory
from utils import run_from_ipython

In [2]:
# Parse arguments

def parse(args=None):
    parser = argparse.ArgumentParser(
        prog='Summarization',
        description='Summarize the transaction history of addresses in the dataset.'
    )
    parser.add_argument('--data', '-d', help='data path', type=str, default='./data')
    parser.add_argument('--out', '-o', help='output path', type=str, default='./data_p')
    parser.add_argument('--end_date', '-e', help='the end date YYYY-MM-DD', type=str, default='2020-06-23')
    return parser.parse_args() if args is None else parser.parse_args(args)
args = parse([]) if run_from_ipython() else parse()
print(args)

Namespace(data='./data', end_date='2020-06-23', out='./data_p')


In [3]:
# Validate arguments

data_path = args.data
out_path = args.out
end_date_string = args.end_date
assert os.path.exists(data_path), 'Data path does not exist: ' + data_path
assert os.path.exists(out_path), 'Output path does not exist: ' + out_path

In [4]:
# Load the Bitcoin dataset

dataset = pd.read_csv(os.path.join(data_path, 'dataset_mymerge.csv'))
print('# of addresses:', len(dataset['address']))
dataset.head(5)
class2label = json.load(open(os.path.join(out_path, 'class2label.json'), 'r', encoding='utf-8'))
label2class = json.load(open(os.path.join(out_path, 'label2class.json'), 'r', encoding='utf-8'))

# of addresses: 60000


In [5]:
# Define an end date and other variables
# For our data are mainly collected in November, 2018, we analysize
# the data from the beginning of Bitcoin (2009) to `to_date` (2018/06/30).

# address_path = '/data/address/'
address_path = os.path.join(data_path, 'address')
to_date = datetime.strptime(end_date_string, '%Y-%m-%d')  # '2018-06-30'
print(to_date)
tx_history = TxHistory(root=data_path, ignore_error=True, to_date=to_date)
print(tx_history)

2020-06-23 00:00:00
Loaded coinbase.pkl. Some coinbase transaction ids:
['dbcfa0738c99b47d83c68dc7c0b0d4579211ba877fbcbc4a96a041651e296038', '677ffea41dfef8205c37ec1c93e4e7c9a618fd42d038e0e431cdddd678f94805', 'c07bff31869169167a1ffb043b9571ea93a6e71a4effbdff4528890a6bc5a3fe', '3bd42b61c33c4773954a747ed8197a9e6c1ef0ba856bb2c27a18fcc99ce35eef', 'dd1f407a9d7e40e5baf086f5094e1be3762b2d261cccdbd8d369d1bff7efeb57']
Processing file: data_p/tx_in_out_sizes1.json
Loaded TxNCounter file data_p/tx_in_out_sizes1.json
Loaded TxN file data_p/tx_in_out_sizes1.json
Processing file: data_p/tx_in_out_sizes2.json
Loaded TxNCounter file data_p/tx_in_out_sizes2.json
Loaded TxN file data_p/tx_in_out_sizes2.json
Processing file: data_p/tx_in_out_sizes3.json
Loaded TxNCounter file data_p/tx_in_out_sizes3.json
Loaded TxN file data_p/tx_in_out_sizes3.json
Processing file: data_p/tx_in_out_sizes4.json
Loaded TxNCounter file data_p/tx_in_out_sizes4.json
Loaded TxN file data_p/tx_in_out_sizes4.json
Processing file

In [6]:
# Address summarization
#
# It takes about twenty minutes in this step.

print('Summarizing address history...')

feature_df = pd.DataFrame(columns=TxHistory.feature_names())
label_df = pd.DataFrame(columns=['class'])
t0 = time.time()

for idx, address in enumerate(tqdm(dataset['address'])):
    address_file = os.path.join(address_path, '{:s}.json'.format(address))
    
    if not os.path.exists(address_file):
        print('Warning: address file not found', address_file)
        continue
    
    address_data = json.load(open(address_file, 'r', encoding='utf-8'))
    tx_history.reset(balance=address_data['balance'])
    
    for tx in address_data['txrefs']:
        print(address_data['txrefs'])
        tx_history.add(tx)
    
    feature = tx_history.summarize()
    if feature is None:
        print('Warning: address', address, 'has no valid txs')
        continue
    feature_df.loc[len(feature_df)] = feature
    label_df.loc[len(label_df)] = [class2label[dataset['class'][idx]]]
    if len(tx_history) == 0:
        print('No transactions related to address', address)

data_df = feature_df.join(label_df)
data_df.to_csv(os.path.join(out_path, 'data.address.csv'), index=0)
print('Finished address-based feature extraction in {:s}'.format(
    str(timedelta(seconds=int(time.time() - t0)))
))

  0%|          | 134/60000 [00:00<00:44, 1335.86it/s]

Summarizing address history...
[{'tx_hash': 'c859c1bc08894099371c5dd2722a4f3793668cad13b18df9d533e4e2a6338fd1', 'tx_input_n': 1, 'block_height': 437060, 'tx_output_n': 1, 'ref_balance': 0.01286292, 'confirmed': '2016-11-02T16:51:04.000000Z'}]


/opt/anaconda3/lib/python3.8/site-packages/numpy/core/fromnumeric.py:3334: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/opt/anaconda3/lib/python3.8/site-packages/numpy/core/_methods.py:161: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
/opt/anaconda3/lib/python3.8/site-packages/numpy/core/fromnumeric.py:3583: RuntimeWarning: Degrees of freedom <= 0 for slice
  return _methods._var(a, axis=axis, dtype=dtype, out=out, ddof=ddof,
/opt/anaconda3/lib/python3.8/site-packages/numpy/core/_methods.py:185: RuntimeWarning: invalid value encountered in true_divide
  arrmean = um.true_divide(
/opt/anaconda3/lib/python3.8/site-packages/numpy/core/_methods.py:209: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
  1%|          | 543/60000 [00:00<00:36, 1620.15it/s]

  2%|▏         | 1076/60000 [00:00<00:29, 2014.60it/s]

  3%|▎         | 1725/60000 [00:00<00:23, 2504.50it/s]

...

[{'tx_hash': '49e343f1524db55edc1d1524e61f9ac8341b1c07efe4301446a7373a46d852bc', 'tx_input_n': 1, 'block_height': 437066, 'tx_output_n': 1, 'ref_balance': 0.00154499, 'confirmed': '2016-11-02T17:49:52.000000Z'}, {'tx_hash': '48fa8ebcc07335ae7e65a3624804c86fab66b83f39db9658812ff567eeb09095', 'tx_input_n': 1, 'block_height': 437221, 'tx_output_n': 1, 'ref_balance': 0.00149349, 'confirmed': '2016-11-03T18:00:30.000000Z'}, {'tx_hash': 'd5c50053db4801e57f27ffc41406638689eb7fbc3c620d39c74f6c7859549002', 'tx_input_n': 1, 'block_height': 437311, 'tx_output_n': 1, 'ref_balance': 0.00178473, 'confirmed': '2016-11-04T11:10:43.000000Z'}]
[{'tx_hash': '49e343f1524db55edc1d1524e61f9ac8341b1c07efe4301446a7373a46d852bc', 'tx_input_n': 1, 'block_height': 437066, 'tx_output_n': 1, 'ref_balance': 0.00154499, 'confirmed': '2016-11-02T17:49:52.000000Z'}, {'tx_hash': '48fa8ebcc07335ae7e65a3624804c86fab66b83f39db9658812ff567eeb09095', 'tx_input_n': 1, 'block_height': 437221, 'tx_output_n': 1, 'ref_balance': 

 99%|█████████▉| 59391/60000 [00:12<00:00, 5168.24it/s]

[{'tx_hash': 'a6ec3c5386c76f350547b26d482e740764a16320e3f2defe10c248e6c37f4f8f', 'tx_input_n': 1, 'block_height': 437033, 'tx_output_n': 2, 'ref_balance': 0.1146, 'confirmed': '2016-11-02T12:40:58.000000Z'}]
[{'tx_hash': 'b1f130000c410614384bfe5293ea29340c4b559b5df1318e62d3288743f2b034', 'tx_input_n': 1, 'block_height': 437283, 'tx_output_n': 2, 'ref_balance': 1.9376, 'confirmed': '2016-11-04T04:44:41.000000Z'}]
[{'tx_hash': '22bddd6582c2922dcd1d5648a8fecfc6d8867b45c2d857ef075e58a15b3fceb6', 'tx_input_n': 1, 'block_height': 437534, 'tx_output_n': 24, 'ref_balance': 0.00853535, 'confirmed': '2016-11-06T02:33:17.000000Z'}]

100%|██████████| 60000/60000 [00:13<00:00, 4607.98it/s]

 ./data/address/1JaSPvdTKX86F9tpQivAxHWcc1aTPRCfNs.json
Finished address-based feature extraction in 0:00:13


In [7]:
# Entity summarization
#
# It takes about fifteen minutes in this step.

print('Summarizing entity history...')
feature_df = pd.DataFrame(columns=TxHistory.feature_names())
label_df = pd.DataFrame(columns=['class'])
t0 = time.time()

for idx, owner in enumerate(tqdm(list(sorted(set(dataset['owner']))))):
    c_labels = dataset[dataset['owner']==owner]['class'].unique()
    for c_label in c_labels:
        tx_history.reset()
        df_tmp = dataset[dataset['owner']==owner]
        df_tmp = df_tmp[df_tmp['class']==c_label]
        for address in df_tmp['address']:
            address_file = os.path.join(address_path, '{:s}.json'.format(address))
            if not os.path.exists(address_file):
                print('Warning: file not found', address_file)
                continue
            address_details = json.load(open(address_file))
            tx_history.add_balance(address_details['balance'])
            for tx in address_details['txrefs']:
                tx_history.add(tx)
        feature = tx_history.summarize()
        if feature is None:
            print('Warning: entity', owner, 'has no valid txs')
            continue
        feature_df.loc[len(feature_df)] = feature
        label_df.loc[len(label_df)] = [class2label[c_label]]
data_df = feature_df.join(label_df)
data_df.to_csv(os.path.join(out_path, 'data.entity.csv'), index=0)
print('Finished entity-based feature extraction in {:s}'.format(
    str(timedelta(seconds=int(time.time() - t0)))
))

Summarizing entity history...


KeyError: 'owner'